In [1]:
#for some feature use mean,for some mode,for some median ,,this kind of operation is not allowableby SimpleImputation
#using Pipeline,ColumnTransformer we can achieve this

In [2]:
import numpy as np
import pandas as pd
from sklearn.impute import SimpleImputer
from sklearn.compose import ColumnTransformer
from sklearn.pipeline import Pipeline

In [3]:
train=pd.read_csv(r'D:\AIML_PROGRAMS\first_model\house-prices-advanced-regression-techniques\train.csv')
test=pd.read_csv(r'D:\AIML_PROGRAMS\first_model\house-prices-advanced-regression-techniques\test.csv')
print('shape of train dataset=',train.shape)
print('shape of test dataset=',test.shape)

shape of train dataset= (1460, 81)
shape of test dataset= (1459, 80)


In [4]:
X_train=train.drop(columns='SalePrice')
y_train=train['SalePrice']#output variable
X_test=test.copy()#shallow copy
print('shape of X_train dataset=',X_train.shape)
print('shape of y_train dataset=',y_train.shape)
print('shape of X_test dataset=',X_test.shape)

shape of X_train dataset= (1460, 80)
shape of y_train dataset= (1460,)
shape of X_test dataset= (1459, 80)


In [5]:
isnull_sum=X_train.isnull().sum()
isnull_sum

Id                 0
MSSubClass         0
MSZoning           0
LotFrontage      259
LotArea            0
                ... 
MiscVal            0
MoSold             0
YrSold             0
SaleType           0
SaleCondition      0
Length: 80, dtype: int64

In [6]:
#finding the numerical var which have missing value
num_vars=X_train.select_dtypes(include=['int64','float64']).columns
num_vars_miss=[var for var in num_vars if isnull_sum[var]>0]
num_vars_miss

['LotFrontage', 'MasVnrArea', 'GarageYrBlt']

In [7]:
X_train[num_vars_miss].isnull().sum()

LotFrontage    259
MasVnrArea       8
GarageYrBlt     81
dtype: int64

In [8]:
#finding the catogarical var which have missing value
cat_vars=X_train.select_dtypes(include='object').columns
cat_vars_miss=[var for var in cat_vars if isnull_sum[var]>0]
cat_vars_miss

['Alley',
 'MasVnrType',
 'BsmtQual',
 'BsmtCond',
 'BsmtExposure',
 'BsmtFinType1',
 'BsmtFinType2',
 'Electrical',
 'FireplaceQu',
 'GarageType',
 'GarageFinish',
 'GarageQual',
 'GarageCond',
 'PoolQC',
 'Fence',
 'MiscFeature']

In [9]:
num_var_mean=['LotFrontage']
num_var_median=[ 'MasVnrArea', 'GarageYrBlt']
cat_vars_mode=['Alley',
 'MasVnrType',
 'BsmtQual',
 'BsmtCond',
 'BsmtExposure',
 'BsmtFinType1',
 'BsmtFinType2',
 'Electrical',
 'FireplaceQu']
#manual / constant value we are gong to fill in below feature
cat_vars_missing=['GarageType',
 'GarageFinish',
 'GarageQual',
 'GarageCond',
 'PoolQC',
 'Fence',
 'MiscFeature']

In [10]:
num_var_mean_imputer=Pipeline(steps=[('imputer',SimpleImputer(strategy='mean'))])
num_var_median_imputer=Pipeline(steps=[('imputer',SimpleImputer(strategy='median'))])
cat_vars_mode_imputer=Pipeline(steps=[('imputer',SimpleImputer(strategy='most_frequent'))])
cat_vars_missing_imputer=Pipeline(steps=[('imputer',SimpleImputer(strategy='constant',fill_value='missing'))])#replace nan with "missing" string,u can give number also


In [11]:
preprocessor=ColumnTransformer(transformers=[
                                ("mean_imputer",num_var_mean_imputer,num_var_mean),
                                ("median_imputer",num_var_median_imputer,num_var_median),
                                ("mode_imputer",cat_vars_mode_imputer,cat_vars_mode),
                                ("missing_imputer",cat_vars_missing_imputer,cat_vars_missing)
                               ]
                 )

In [12]:
preprocessor.fit(X_train)

ColumnTransformer(transformers=[('mean_imputer',
                                 Pipeline(steps=[('imputer', SimpleImputer())]),
                                 ['LotFrontage']),
                                ('median_imputer',
                                 Pipeline(steps=[('imputer',
                                                  SimpleImputer(strategy='median'))]),
                                 ['MasVnrArea', 'GarageYrBlt']),
                                ('mode_imputer',
                                 Pipeline(steps=[('imputer',
                                                  SimpleImputer(strategy='most_frequent'))]),
                                 ['Alley', 'MasVnrType', 'BsmtQual', 'BsmtCond',
                                  'BsmtExposure', 'BsmtFinType1',
                                  'BsmtFinType2', 'Electrical',
                                  'FireplaceQu']),
                                ('missing_imputer',
                                 Pipeline(steps=[('imputer',
                                                  SimpleImputer(fill_value='missing',
                                                                strategy='constant'))]),
                                 ['GarageType', 'GarageFinish', 'GarageQual',
                                  'GarageCond', 'PoolQC', 'Fence',
                                  'MiscFeature'])])

In [13]:
#to check what value are calculated by transformer
preprocessor.named_transformers_['mean_imputer'].named_steps['imputer'].statistics_

array([70.04995837])

In [14]:
train['LotFrontage'].mean()

70.04995836802665

In [15]:
#as u see calculated correct

In [16]:
preprocessor.named_transformers_['mode_imputer'].named_steps['imputer'].statistics_

array(['Grvl', 'None', 'TA', 'TA', 'No', 'Unf', 'Unf', 'SBrkr', 'Gd'],
      dtype=object)

In [17]:
preprocessor.named_transformers_['median_imputer'].named_steps['imputer'].statistics_

array([   0., 1980.])

In [18]:
X_train#see calculated values are not imputed in actual data set,,

Id  MSSubClass MSZoning  LotFrontage  LotArea Street Alley LotShape  \
0        1          60       RL         65.0     8450   Pave   NaN      Reg   
1        2          20       RL         80.0     9600   Pave   NaN      Reg   
2        3          60       RL         68.0    11250   Pave   NaN      IR1   
3        4          70       RL         60.0     9550   Pave   NaN      IR1   
4        5          60       RL         84.0    14260   Pave   NaN      IR1   
...    ...         ...      ...          ...      ...    ...   ...      ...   
1455  1456          60       RL         62.0     7917   Pave   NaN      Reg   
1456  1457          20       RL         85.0    13175   Pave   NaN      Reg   
1457  1458          70       RL         66.0     9042   Pave   NaN      Reg   
1458  1459          20       RL         68.0     9717   Pave   NaN      Reg   
1459  1460          20       RL         75.0     9937   Pave   NaN      Reg   

     LandContour Utilities  ... ScreenPorch PoolArea PoolQC  Fence  \
0            Lvl    AllPub  ...           0        0    NaN    NaN   
1            Lvl    AllPub  ...           0        0    NaN    NaN   
2            Lvl    AllPub  ...           0        0    NaN    NaN   
3            Lvl    AllPub  ...           0        0    NaN    NaN   
4            Lvl    AllPub  ...           0        0    NaN    NaN   
...          ...       ...  ...         ...      ...    ...    ...   
1455         Lvl    AllPub  ...           0        0    NaN    NaN   
1456         Lvl    AllPub  ...           0        0    NaN  MnPrv   
1457         Lvl    AllPub  ...           0        0    NaN  GdPrv   
1458         Lvl    AllPub  ...           0        0    NaN    NaN   
1459         Lvl    AllPub  ...           0        0    NaN    NaN   

     MiscFeature MiscVal MoSold  YrSold  SaleType  SaleCondition  
0            NaN       0      2    2008        WD         Normal  
1            NaN       0      5    2007        WD         Normal  
2            NaN       0      9    2008        WD         Normal  
3            NaN       0      2    2006        WD        Abnorml  
4            NaN       0     12    2008        WD         Normal  
...          ...     ...    ...     ...       ...            ...  
1455         NaN       0      8    2007        WD         Normal  
1456         NaN       0      2    2010        WD         Normal  
1457        Shed    2500      5    2010        WD         Normal  
1458         NaN       0      4    2010        WD         Normal  
1459         NaN       0      6    2008        WD         Normal  

[1460 rows x 80 columns]

In [19]:
X_train_clean=preprocessor.transform(X_train)#preprocessor contains calculated value in its memory space,and we are going to transform t in X_train and store in X_train_clean
#note-->return 2d array so dont assign in X_train (original dataset)
X_test_clean=preprocessor.transform(X_test)
X_train_clean

array([[65.0, 196.0, 2003.0, ..., 'missing', 'missing', 'missing'],
       [80.0, 0.0, 1976.0, ..., 'missing', 'missing', 'missing'],
       [68.0, 162.0, 2001.0, ..., 'missing', 'missing', 'missing'],
       ...,
       [66.0, 0.0, 1941.0, ..., 'missing', 'GdPrv', 'Shed'],
       [68.0, 0.0, 1950.0, ..., 'missing', 'missing', 'missing'],
       [75.0, 0.0, 1965.0, ..., 'missing', 'missing', 'missing']],
      dtype=object)

In [20]:
preprocessor.transformers_

[('mean_imputer',
  Pipeline(steps=[('imputer', SimpleImputer())]),
  ['LotFrontage']),
 ('median_imputer',
  Pipeline(steps=[('imputer', SimpleImputer(strategy='median'))]),
  ['MasVnrArea', 'GarageYrBlt']),
 ('mode_imputer',
  Pipeline(steps=[('imputer', SimpleImputer(strategy='most_frequent'))]),
  ['Alley',
   'MasVnrType',
   'BsmtQual',
   'BsmtCond',
   'BsmtExposure',
   'BsmtFinType1',
   'BsmtFinType2',
   'Electrical',
   'FireplaceQu']),
 ('missing_imputer',
  Pipeline(steps=[('imputer',
                   SimpleImputer(fill_value='missing', strategy='constant'))]),
  ['GarageType',
   'GarageFinish',
   'GarageQual',
   'GarageCond',
   'PoolQC',
   'Fence',
   'MiscFeature']),
 ('remainder',
  'drop',
  [0,
   1,
   2,
   4,
   5,
   7,
   8,
   9,
   10,
   11,
   12,
   13,
   14,
   15,
   16,
   17,
   18,
   19,
   20,
   21,
   22,
   23,
   24,
   27,
   28,
   29,
   34,
   36,
   37,
   38,
   39,
   40,
   41,
   43,
   44,
   45,
   46,
   47,
   48,
   49,
   

In [21]:
#inside remainder droped column index is ther
#ie;columns/features with no missing value is droped automatically by ColumnTransformer method
#so use transformer=[(....,transformer='passthrough')],,so that columns with no missing values are not froped and retained

In [22]:
#now converting 2d array(X_train_clean) to data frame
X_train_clean_mis_var=pd.DataFrame(X_train_clean,columns=num_var_mean+num_var_median+cat_vars_mode+cat_vars_missing)#Concatination order should be same as u declared above
X_train_clean_mis_var

LotFrontage MasVnrArea GarageYrBlt Alley MasVnrType BsmtQual BsmtCond  \
0           65.0      196.0      2003.0  Grvl    BrkFace       Gd       TA   
1           80.0        0.0      1976.0  Grvl       None       Gd       TA   
2           68.0      162.0      2001.0  Grvl    BrkFace       Gd       TA   
3           60.0        0.0      1998.0  Grvl       None       TA       Gd   
4           84.0      350.0      2000.0  Grvl    BrkFace       Gd       TA   
...          ...        ...         ...   ...        ...      ...      ...   
1455        62.0        0.0      1999.0  Grvl       None       Gd       TA   
1456        85.0      119.0      1978.0  Grvl      Stone       Gd       TA   
1457        66.0        0.0      1941.0  Grvl       None       TA       Gd   
1458        68.0        0.0      1950.0  Grvl       None       TA       TA   
1459        75.0        0.0      1965.0  Grvl       None       TA       TA   

     BsmtExposure BsmtFinType1 BsmtFinType2 Electrical FireplaceQu GarageType  \
0              No          GLQ          Unf      SBrkr          Gd     Attchd   
1              Gd          ALQ          Unf      SBrkr          TA     Attchd   
2              Mn          GLQ          Unf      SBrkr          TA     Attchd   
3              No          ALQ          Unf      SBrkr          Gd     Detchd   
4              Av          GLQ          Unf      SBrkr          TA     Attchd   
...           ...          ...          ...        ...         ...        ...   
1455           No          Unf          Unf      SBrkr          TA     Attchd   
1456           No          ALQ          Rec      SBrkr          TA     Attchd   
1457           No          GLQ          Unf      SBrkr          Gd     Attchd   
1458           Mn          GLQ          Rec      FuseA          Gd     Attchd   
1459           No          BLQ          LwQ      SBrkr          Gd     Attchd   

     GarageFinish GarageQual GarageCond   PoolQC    Fence MiscFeature  
0             RFn         TA         TA  missing  missing     missing  
1             RFn         TA         TA  missing  missing     missing  
2             RFn         TA         TA  missing  missing     missing  
3             Unf         TA         TA  missing  missing     missing  
4             RFn         TA         TA  missing  missing     missing  
...           ...        ...        ...      ...      ...         ...  
1455          RFn         TA         TA  missing  missing     missing  
1456          Unf         TA         TA  missing    MnPrv     missing  
1457          RFn         TA         TA  missing    GdPrv        Shed  
1458          Unf         TA         TA  missing  missing     missing  
1459          Fin         TA         TA  missing  missing     missing  

[1460 rows x 19 columns]

In [23]:
X_train

Id  MSSubClass MSZoning  LotFrontage  LotArea Street Alley LotShape  \
0        1          60       RL         65.0     8450   Pave   NaN      Reg   
1        2          20       RL         80.0     9600   Pave   NaN      Reg   
2        3          60       RL         68.0    11250   Pave   NaN      IR1   
3        4          70       RL         60.0     9550   Pave   NaN      IR1   
4        5          60       RL         84.0    14260   Pave   NaN      IR1   
...    ...         ...      ...          ...      ...    ...   ...      ...   
1455  1456          60       RL         62.0     7917   Pave   NaN      Reg   
1456  1457          20       RL         85.0    13175   Pave   NaN      Reg   
1457  1458          70       RL         66.0     9042   Pave   NaN      Reg   
1458  1459          20       RL         68.0     9717   Pave   NaN      Reg   
1459  1460          20       RL         75.0     9937   Pave   NaN      Reg   

     LandContour Utilities  ... ScreenPorch PoolArea PoolQC  Fence  \
0            Lvl    AllPub  ...           0        0    NaN    NaN   
1            Lvl    AllPub  ...           0        0    NaN    NaN   
2            Lvl    AllPub  ...           0        0    NaN    NaN   
3            Lvl    AllPub  ...           0        0    NaN    NaN   
4            Lvl    AllPub  ...           0        0    NaN    NaN   
...          ...       ...  ...         ...      ...    ...    ...   
1455         Lvl    AllPub  ...           0        0    NaN    NaN   
1456         Lvl    AllPub  ...           0        0    NaN  MnPrv   
1457         Lvl    AllPub  ...           0        0    NaN  GdPrv   
1458         Lvl    AllPub  ...           0        0    NaN    NaN   
1459         Lvl    AllPub  ...           0        0    NaN    NaN   

     MiscFeature MiscVal MoSold  YrSold  SaleType  SaleCondition  
0            NaN       0      2    2008        WD         Normal  
1            NaN       0      5    2007        WD         Normal  
2            NaN       0      9    2008        WD         Normal  
3            NaN       0      2    2006        WD        Abnorml  
4            NaN       0     12    2008        WD         Normal  
...          ...     ...    ...     ...       ...            ...  
1455         NaN       0      8    2007        WD         Normal  
1456         NaN       0      2    2010        WD         Normal  
1457        Shed    2500      5    2010        WD         Normal  
1458         NaN       0      4    2010        WD         Normal  
1459         NaN       0      6    2008        WD         Normal  

[1460 rows x 80 columns]

In [24]:
pd.set_option('display.max_rows',None)
pd.set_option('display.max_columns',None)
X_train.isnull().sum()

Id                  0
MSSubClass          0
MSZoning            0
LotFrontage       259
LotArea             0
Street              0
Alley            1369
LotShape            0
LandContour         0
Utilities           0
LotConfig           0
LandSlope           0
Neighborhood        0
Condition1          0
Condition2          0
BldgType            0
HouseStyle          0
OverallQual         0
OverallCond         0
YearBuilt           0
YearRemodAdd        0
RoofStyle           0
RoofMatl            0
Exterior1st         0
Exterior2nd         0
MasVnrType          8
MasVnrArea          8
ExterQual           0
ExterCond           0
Foundation          0
BsmtQual           37
BsmtCond           37
BsmtExposure       38
BsmtFinType1       37
BsmtFinSF1          0
BsmtFinType2       38
BsmtFinSF2          0
BsmtUnfSF           0
TotalBsmtSF         0
Heating             0
HeatingQC           0
CentralAir          0
Electrical          1
1stFlrSF            0
2ndFlrSF            0
LowQualFin

In [25]:
X_train['Alley'].value_counts()

Grvl    50
Pave    41
Name: Alley, dtype: int64

In [26]:
X_train_clean_mis_var['Alley'].value_counts()

Grvl    1419
Pave      41
Name: Alley, dtype: int64

In [27]:
#as u see values are updated  correctly

In [28]:
X_train_clean_mis_var.isnull().sum()

LotFrontage     0
MasVnrArea      0
GarageYrBlt     0
Alley           0
MasVnrType      0
BsmtQual        0
BsmtCond        0
BsmtExposure    0
BsmtFinType1    0
BsmtFinType2    0
Electrical      0
FireplaceQu     0
GarageType      0
GarageFinish    0
GarageQual      0
GarageCond      0
PoolQC          0
Fence           0
MiscFeature     0
dtype: int64

In [34]:
#missing value are replaced with mean,median,mode,constant respectivelys

In [ ]:
#now reflect the modified/cleaned feture in original dataset)X_train

In [30]:
modified_feature=['LotFrontage', 'MasVnrArea', 'GarageYrBlt', 'Alley', 'MasVnrType',
       'BsmtQual', 'BsmtCond', 'BsmtExposure', 'BsmtFinType1', 'BsmtFinType2',
       'Electrical', 'FireplaceQu', 'GarageType', 'GarageFinish', 'GarageQual',
       'GarageCond', 'PoolQC', 'Fence', 'MiscFeature']
for feature in modified_feature:
    X_train[feature]=X_train_clean_mis_var[feature]


In [31]:
X_train.shape

(1460, 80)

In [35]:
X_train

Id  MSSubClass MSZoning LotFrontage  LotArea Street Alley LotShape  \
0        1          60       RL        65.0     8450   Pave  Grvl      Reg   
1        2          20       RL        80.0     9600   Pave  Grvl      Reg   
2        3          60       RL        68.0    11250   Pave  Grvl      IR1   
3        4          70       RL        60.0     9550   Pave  Grvl      IR1   
4        5          60       RL        84.0    14260   Pave  Grvl      IR1   
5        6          50       RL        85.0    14115   Pave  Grvl      IR1   
6        7          20       RL        75.0    10084   Pave  Grvl      Reg   
7        8          60       RL   70.049958    10382   Pave  Grvl      IR1   
8        9          50       RM        51.0     6120   Pave  Grvl      Reg   
9       10         190       RL        50.0     7420   Pave  Grvl      Reg   
10      11          20       RL        70.0    11200   Pave  Grvl      Reg   
11      12          60       RL        85.0    11924   Pave  Grvl      IR1   
12      13          20       RL   70.049958    12968   Pave  Grvl      IR2   
13      14          20       RL        91.0    10652   Pave  Grvl      IR1   
14      15          20       RL   70.049958    10920   Pave  Grvl      IR1   
15      16          45       RM        51.0     6120   Pave  Grvl      Reg   
16      17          20       RL   70.049958    11241   Pave  Grvl      IR1   
17      18          90       RL        72.0    10791   Pave  Grvl      Reg   
18      19          20       RL        66.0    13695   Pave  Grvl      Reg   
19      20          20       RL        70.0     7560   Pave  Grvl      Reg   
20      21          60       RL       101.0    14215   Pave  Grvl      IR1   
21      22          45       RM        57.0     7449   Pave  Grvl      Reg   
22      23          20       RL        75.0     9742   Pave  Grvl      Reg   
23      24         120       RM        44.0     4224   Pave  Grvl      Reg   
24      25          20       RL   70.049958     8246   Pave  Grvl      IR1   
25      26          20       RL       110.0    14230   Pave  Grvl      Reg   
26      27          20       RL        60.0     7200   Pave  Grvl      Reg   
27      28          20       RL        98.0    11478   Pave  Grvl      Reg   
28      29          20       RL        47.0    16321   Pave  Grvl      IR1   
29      30          30       RM        60.0     6324   Pave  Grvl      IR1   
30      31          70  C (all)        50.0     8500   Pave  Pave      Reg   
31      32          20       RL   70.049958     8544   Pave  Grvl      IR1   
32      33          20       RL        85.0    11049   Pave  Grvl      Reg   
33      34          20       RL        70.0    10552   Pave  Grvl      IR1   
34      35         120       RL        60.0     7313   Pave  Grvl      Reg   
35      36          60       RL       108.0    13418   Pave  Grvl      Reg   
36      37          20       RL       112.0    10859   Pave  Grvl      Reg   
37      38          20       RL        74.0     8532   Pave  Grvl      Reg   
38      39          20       RL        68.0     7922   Pave  Grvl      Reg   
39      40          90       RL        65.0     6040   Pave  Grvl      Reg   
40      41          20       RL        84.0     8658   Pave  Grvl      Reg   
41      42          20       RL       115.0    16905   Pave  Grvl      Reg   
42      43          85       RL   70.049958     9180   Pave  Grvl      IR1   
43      44          20       RL   70.049958     9200   Pave  Grvl      IR1   
44      45          20       RL        70.0     7945   Pave  Grvl      Reg   
45      46         120       RL        61.0     7658   Pave  Grvl      Reg   
46      47          50       RL        48.0    12822   Pave  Grvl      IR1   
47      48          20       FV        84.0    11096   Pave  Grvl      Reg   
48      49         190       RM        33.0     4456   Pave  Grvl      Reg   
49      50          20       RL        66.0     7742   Pave  Grvl      Reg   
50      51          60       R

In [37]:
X_train.isnull().sum()

Id               0
MSSubClass       0
MSZoning         0
LotFrontage      0
LotArea          0
Street           0
Alley            0
LotShape         0
LandContour      0
Utilities        0
LotConfig        0
LandSlope        0
Neighborhood     0
Condition1       0
Condition2       0
BldgType         0
HouseStyle       0
OverallQual      0
OverallCond      0
YearBuilt        0
YearRemodAdd     0
RoofStyle        0
RoofMatl         0
Exterior1st      0
Exterior2nd      0
MasVnrType       0
MasVnrArea       0
ExterQual        0
ExterCond        0
Foundation       0
BsmtQual         0
BsmtCond         0
BsmtExposure     0
BsmtFinType1     0
BsmtFinSF1       0
BsmtFinType2     0
BsmtFinSF2       0
BsmtUnfSF        0
TotalBsmtSF      0
Heating          0
HeatingQC        0
CentralAir       0
Electrical       0
1stFlrSF         0
2ndFlrSF         0
LowQualFinSF     0
GrLivArea        0
BsmtFullBath     0
BsmtHalfBath     0
FullBath         0
HalfBath         0
BedroomAbvGr     0
KitchenAbvGr

In [ ]:
#X_train is cleaned succefully